# JijModeling 1.12.1 Release Notes

## Feature Enhancements

### Human Readable Errors in Interpreters

Now [`Interpreter`](https://jij-inc.github.io/JijModeling-Tutorials/apis/jijmodeling.html#Interpreter) fails with more human-readable error message. For example:

In [15]:
import jijmodeling as jm

D = jm.Placeholder("D", dtype=jm.DataType.INTEGER)
T = jm.Placeholder("T", dtype=jm.DataType.INTEGER)
N = jm.Placeholder("N", dtype=jm.DataType.INTEGER)
H = jm.Placeholder("H", shape=(D, T, N))
R = jm.Placeholder("R", shape=(D, N))

x = jm.BinaryVar("x", shape=(D, T, N))
d = jm.Element("d", belong_to=(0, D))
t = jm.Element("t", belong_to=(0, T))
i = jm.Element("i", belong_to=(0, N))

problem = jm.Problem(name="shift_optimization")
problem += jm.Constraint("night_shift", R[d+1, i] <= x[d, T-1, i], forall=[d, i])
problem += jm.sum([d, t, i], x[d, t, i])

problem

In [17]:
num_days = 7
num_times = 3
num_people = 5

data = problem.generate_random_dataset(
    options={
        "D": {"value": num_days},
        "T": {"value": num_times},
        
        "N": {"value": num_people},
    }
)
interp = jm.Interpreter(data)

try:
    interp.eval_problem(problem)
except Exception as e:
    print(e)

Traceback (most recent last):
    while evaluating Problem `shift_optimization',
    while evaluating constraint: `night_shift',
    while evaluating expression `R[d + 1, i] - x[d, T - 1, i]',
    while evaluating expression `R[d + 1, i]',

IndexError: Index [7, 0] is out of range for shape [7, 5]


## Bugfixes

### Fixes the Performance Bug in `Interpreter.eval_*`.

Previously, evaluating expressions with `Interpreter` takes much more times than intended.
This was due to the direct call to the arithmetic operations on OMMX `Function`s, which goes through conversion between intermediate expressions and re-allocates memory from the ground up. This results in quadratic performance degradation in some summation operations.

Now JijModeling uses dedicated intermediate form of functions, so the overhead of conversion should be greatly tamed now.